In [1]:
latest_gameweek = 12

In [2]:
import pandas as pd
import numpy as np
from pathlib import Path
from pulp import LpMaximize, LpProblem, LpStatus, lpSum, LpVariable

# Solver

In [3]:
def optimize(df, max_price, expected_column, captain_double_points=True):
    '''Function for solving the optimization problem.'''    
    # PRELIMINARIES

    # Create the model
    model = LpProblem(name="FPL", sense=LpMaximize)    
    variables = [LpVariable(name=f'{ix}', cat='Binary') for ix in df.index]
    captaincy_variables = [LpVariable(name=f'cap_{ix}', cat='Binary') for ix in df.index]
    prices = [df.loc[ix,'price'] for ix in df.index]
    # measure of player quality
    expected_points = [df.loc[ix,expected_column] for ix in df.index]
    goalkeepers = [1.0 if df.loc[ix,'position']=='GK' else 0.0 for ix in df.index]
    defenders = [1.0 if df.loc[ix,'position']=='DEF' else 0.0 for ix in df.index]
    midfielders = [1.0 if df.loc[ix,'position']=='MID' else 0.0 for ix in df.index]
    forwards = [1.0 if df.loc[ix,'position']=='FWD' else 0.0 for ix in df.index]
    teams = []
    for team in df['team'].unique():
        teams.append( [1.0 if df.loc[ix,'team']==team else 0.0 for ix in df.index] )

    # CONSTRAINTS

    # select 11 players
    model += lpSum(variables) == 11
    # select 1 captain
    model += lpSum(captaincy_variables) == 1
    # captain must be one of the 11 players in the team
    for i in range(0,len(variables)):
        model += captaincy_variables[i] <= variables[i]
    # set maximum price for starting 11
    model += np.dot(prices,variables) <= max_price
    # only 1 goalkeeper
    model += np.dot(goalkeepers,variables) == 1
    # at least 3 defenders
    model += np.dot(defenders,variables) >= 3
    # at most 5 defenders
    model += np.dot(defenders,variables) <= 5
    # at most 5 midfielders
    model += np.dot(midfielders,variables) <= 5
    # at least 1 forward
    model += np.dot(forwards,variables) >= 1
    # at most 3 forwards
    model += np.dot(forwards,variables) <= 3
    # max 3 players from any given team
    for team in teams:
        model += np.dot(team,variables) <= 3

    # OBJECTIVE
    if captain_double_points:
        # the second part doubles the captain's points
        model += np.dot(expected_points,variables) + np.dot(expected_points,captaincy_variables)
    else:
        model += np.dot(expected_points,variables)

    # SOLVE OPTIMIZATION

    status = model.solve()
    print(f'Status: {LpStatus[model.status]}')
    #print(f'Mean total points per gameweek: {model.objective.value()}')

    players = [str(var) for var in model.variables() if var.value()==1]
    captain = [player for player in players if 'cap' in player]
    captain = int(captain[0].replace('cap_', ''))
    players = [int(player) for player in players if 'cap' not in player]
    dream_team = df.loc[players]
    cost = (dream_team['price']).sum()
    exp_points = dream_team[expected_column].sum() + df.loc[captain, expected_column]
    print(f'Cost: {cost}')
    print(f'Expected points per week: {exp_points}')
    
    display(dream_team[['position','name', 'team', 'price', expected_column]].sort_values('position'))
    
    return players

# Data

In [4]:
path = Path(f'../data/predictions/gameweek{latest_gameweek}.csv')
projections = pd.read_csv(path, index_col=0)
projections.head(5)

name  element_type  home  corners_and_indirect_freekicks_order  \
0  Aaron Cresswell             2     0                                   3.0   
1  Aaron Cresswell             2     1                                   3.0   
2  Aaron Cresswell             2     0                                   3.0   
3  Aaron Cresswell             2     0                                   3.0   
4  Aaron Cresswell             2     1                                   3.0   

   creativity_rank  direct_freekicks_order  ict_index_rank  influence_rank  \
0              323                     NaN             402             402   
1              323                     NaN             402             402   
2              323                     NaN             402             402   
3              323                     NaN             402             402   
4              323                     NaN             402             402   

   minutes  now_cost  ...  gameweek_xG_expanding_per90  \
0       85        42  ...                     0.024163   
1       85        42  ...                     0.024163   
2       85        42  ...                     0.024163   
3       85        42  ...                     0.024163   
4       85        42  ...                     0.024163   

   gameweek_xA_expanding_per90  gameweek_xGA_expanding_per90  \
0                      0.14652                      1.379997   
1                      0.14652                      1.379997   
2                      0.14652                      1.379997   
3                      0.14652                      1.379997   
4                      0.14652                      1.379997   

   gameweek_xPoints_expanding_per90  xG_overperformance  team_name  \
0                          3.715587            1.950078   West Ham   
1                          3.715587            1.950078   West Ham   
2                          3.715587            1.950078   West Ham   
3                          3.715587            1.950078   West Ham   
4                          3.715587            1.950078   West Ham   

    opponent_team                  date  gameweek  expected_points  
0         Burnley  2023-11-25T15:00:00Z        13         2.938058  
1  Crystal Palace  2023-12-03T14:00:00Z        14         2.974322  
2       Tottenham  2023-12-07T20:15:00Z        15         2.310379  
3          Fulham  2023-12-10T14:00:00Z        16         2.954327  
4          Wolves  2023-12-17T14:00:00Z        17         3.141623  

[5 rows x 113 columns]

In [5]:
# decay for future projected points to model uncertainty increasing over time
decay_coeff = 0.875
projections['expected_points_with_decay'] = ( projections['expected_points']*decay_coeff
                                              **(projections['gameweek']-1) )
projections.head(5)

name  element_type  home  corners_and_indirect_freekicks_order  \
0  Aaron Cresswell             2     0                                   3.0   
1  Aaron Cresswell             2     1                                   3.0   
2  Aaron Cresswell             2     0                                   3.0   
3  Aaron Cresswell             2     0                                   3.0   
4  Aaron Cresswell             2     1                                   3.0   

   creativity_rank  direct_freekicks_order  ict_index_rank  influence_rank  \
0              323                     NaN             402             402   
1              323                     NaN             402             402   
2              323                     NaN             402             402   
3              323                     NaN             402             402   
4              323                     NaN             402             402   

   minutes  now_cost  ...  gameweek_xA_expanding_per90  \
0       85        42  ...                      0.14652   
1       85        42  ...                      0.14652   
2       85        42  ...                      0.14652   
3       85        42  ...                      0.14652   
4       85        42  ...                      0.14652   

   gameweek_xGA_expanding_per90  gameweek_xPoints_expanding_per90  \
0                      1.379997                          3.715587   
1                      1.379997                          3.715587   
2                      1.379997                          3.715587   
3                      1.379997                          3.715587   
4                      1.379997                          3.715587   

   xG_overperformance  team_name   opponent_team                  date  \
0            1.950078   West Ham         Burnley  2023-11-25T15:00:00Z   
1            1.950078   West Ham  Crystal Palace  2023-12-03T14:00:00Z   
2            1.950078   West Ham       Tottenham  2023-12-07T20:15:00Z   
3            1.950078   West Ham          Fulham  2023-12-10T14:00:00Z   
4            1.950078   West Ham          Wolves  2023-12-17T14:00:00Z   

   gameweek  expected_points  expected_points_with_decay  
0        13         2.938058                    0.591775  
1        14         2.974322                    0.524195  
2        15         2.310379                    0.356284  
3        16         2.954327                    0.398639  
4        17         3.141623                    0.370922  

[5 rows x 114 columns]

In [6]:
my_gameweeks = np.arange(latest_gameweek+1, latest_gameweek+11, 1)
#my_gameweeks = np.arange(latest_gameweek+1, latest_gameweek+4, 1)
#my_gameweeks = np.arange(latest_gameweek+2, latest_gameweek+12, 1)
df = projections[projections['gameweek'].isin(my_gameweeks)].groupby(by=['name', 'team_name']).sum()\
                                                        [['expected_points','expected_points_with_decay']]
df['number_of_games'] = (
    projections[projections['gameweek']
    .isin(my_gameweeks)]
    .groupby(['name', 'team_name'])
    .count()['element_type']
)

df = df.reset_index()

df['position'] = [projections.loc[projections['name']==name, 'element_type'].values[0] for name in df['name']]
position_dict={1:'GK', 2:'DEF', 3:'MID', 4:'FWD'}
df['position'] = df['position'].map(position_dict)
df['position'] = pd.Categorical(df['position'], ['GK','DEF','MID','FWD'])

df['price'] = [projections.loc[projections['name']==name, 'now_cost'].values[0] for name in df['name']]
df['price'] = df['price'] / 10.0

df['team'] = [projections.loc[projections['name']==name, 'team_name'].values[0] for name in df['name']]

df

name       team_name  expected_points  \
0             Aaron Cresswell        West Ham        27.576262   
1                Aaron Hickey       Brentford        22.229756   
2              Aaron Ramsdale         Arsenal        37.590208   
3                Aaron Ramsey         Burnley        19.555391   
4           Aaron Wan-Bissaka  Manchester Utd        30.712928   
..                        ...             ...              ...   
466               Yoane Wissa       Brentford        34.353043   
467           Youri Tielemans     Aston Villa        23.623032   
468  Youssef Ramalho Chermiti         Everton        15.104875   
469             Yves Bissouma       Tottenham        22.258786   
470              Zeki Amdouni         Burnley        22.763992   

     expected_points_with_decay  number_of_games position  price  \
0                      3.286763               10      DEF    4.2   
1                      2.674367                9      DEF    4.5   
2                      4.444686               10       GK    5.0   
3                      2.356071               10      MID    5.0   
4                      3.577678               10      DEF    4.4   
..                          ...              ...      ...    ...   
466                    4.138889                9      FWD    5.9   
467                    2.785157               10      MID    5.6   
468                    1.788368               10      FWD    4.9   
469                    2.616996               10      MID    5.0   
470                    2.746605               10      FWD    5.3   

               team  
0          West Ham  
1         Brentford  
2           Arsenal  
3           Burnley  
4    Manchester Utd  
..              ...  
466       Brentford  
467     Aston Villa  
468         Everton  
469       Tottenham  
470         Burnley  

[471 rows x 8 columns]

# Optimization

In [7]:
team_value = 100.5
money_in_the_bank = 2.4
allowed_bench_value = 17.5
max_price = team_value + money_in_the_bank - allowed_bench_value

In [8]:
ban = []

# ban some cheap keepers in good teams who don't actually play
cheap_keepers = ['Robin Olsen', 'Jason Steele']
cheap_keepers_ix = df[df['name'].isin(cheap_keepers)].index
ban = ban + list(cheap_keepers_ix)

# ban given outfield players
ban_field = ['Kevin De Bruyne', 'Andrew Robertson', 'Pervis Estupiñán', 'Sven Botman', 'Luke Shaw',]
ban_field_ix = df[df['name'].isin(ban_field)].index
ban = ban + list(ban_field_ix)

my_df = df.drop(ban).copy()

In [9]:
players = optimize(my_df, max_price, 'expected_points_with_decay')

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/aa0c313d1ce847448e74f228a4c78984-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/aa0c313d1ce847448e74f228a4c78984-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 498 COLUMNS
At line 6747 RHS
At line 7241 BOUNDS
At line 8170 ENDATA
Problem MODEL has 493 rows, 928 columns and 3464 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 71.3219 - 0.00 seconds
Cgl0004I processed model has 491 rows, 928 columns (928 integer (928 of which binary)) and 3248 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.785714
Cbc0038I Pass   1: suminf.    0.3

position                    name            team  price  \
108       GK       David Raya Martin         Arsenal    4.9   
216      DEF        Joachim Andersen  Crystal Palace    5.1   
258      DEF         Kieran Trippier   Newcastle Utd    7.0   
444      DEF  Trent Alexander-Arnold       Liverpool    7.9   
165      MID           Heung-Min Son       Tottenham    9.7   
331      MID           Mohamed Salah       Liverpool   13.0   
380      MID         Raheem Sterling         Chelsea    6.9   
69       MID            Bryan Mbeumo       Brentford    6.9   
70       MID             Bukayo Saka         Arsenal    8.7   
349      FWD         Nicolas Jackson         Chelsea    6.8   
363      FWD           Ollie Watkins     Aston Villa    8.5   

     expected_points_with_decay  
108                    4.484008  
216                    4.339639  
258                    5.419818  
444                    5.577529  
165                    6.634525  
331                    7.447358  
380                    5.589205  
69                     6.073688  
70                     6.922026  
349                    5.053802  
363                    6.194676

In [10]:
sigma=0.5
simulation_rounds = 500
next_gameweek=latest_gameweek+1

ban = []

# ban some cheap keepers in good teams who don't actually play
cheap_keepers = ['Robin Olsen']
cheap_keepers_ix = df[df['name'].isin(cheap_keepers)].index
ban = ban + list(cheap_keepers_ix)

# ban given outfield players
ban_field = ['Kevin De Bruyne', 'Andrew Robertson']
ban_field_ix = df[df['name'].isin(ban_field)].index
ban = ban + list(ban_field_ix)

results = []
for i in range(simulation_rounds):
 
    # add random noise to expected points (a fixed offset for every projection of any given player)
    projections['expected_points_with_noise'] = (projections
    .groupby('name')
    .apply(lambda x: x['expected_points']+np.random.normal(0,sigma))
    .reset_index()
    .sort_values('level_1')
    ['expected_points']
    .values
    )

    # decay
    projections['expected_points_with_noise_with_decay'] = ( projections['expected_points_with_noise']*decay_coeff
                                              **(projections['gameweek']-next_gameweek) )

    df['expected_points_with_noise_with_decay'] = projections[projections['gameweek'].isin(my_gameweeks)].groupby(by=['name', 'team_name']).sum()\
                                                            ['expected_points_with_noise_with_decay'].values

    my_df = df.drop(ban).copy()
    
    players = optimize(my_df, max_price, 'expected_points_with_noise_with_decay')

    results.append(players)
    

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/6fcdfa5227e141d895c7744df6718261-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/6fcdfa5227e141d895c7744df6718261-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 502 COLUMNS
At line 6806 RHS
At line 7304 BOUNDS
At line 8241 ENDATA
Problem MODEL has 497 rows, 936 columns and 3495 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 364.216 - 0.00 seconds
Cgl0004I processed model has 495 rows, 936 columns (936 integer (936 of which binary)) and 3276 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.861111
Cbc0038I Pass   1: suminf.    0.6

position                    name             team  price  \
392       GK          Robert Sánchez          Chelsea    4.6   
444      DEF  Trent Alexander-Arnold        Liverpool    7.9   
451      DEF         Virgil van Dijk        Liverpool    6.1   
48       DEF         Aymeric Laporte  Manchester City    5.0   
165      MID           Heung-Min Son        Tottenham    9.7   
206      MID            Jarrod Bowen         West Ham    7.7   
331      MID           Mohamed Salah        Liverpool   13.0   
69       MID            Bryan Mbeumo        Brentford    6.9   
70       MID             Bukayo Saka          Arsenal    8.7   
349      FWD         Nicolas Jackson          Chelsea    6.8   
363      FWD           Ollie Watkins      Aston Villa    8.5   

     expected_points_with_noise_with_decay  
392                              25.876313  
444                              28.334588  
451                              24.841133  
48                               25.132473  
165                              34.861485  
206                              30.114331  
331                              31.004254  
69                               31.354490  
70                               35.573818  
349                              28.336467  
363                              32.126071

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/5548135c7da5487994a43b72884ed3d2-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/5548135c7da5487994a43b72884ed3d2-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 502 COLUMNS
At line 6806 RHS
At line 7304 BOUNDS
At line 8241 ENDATA
Problem MODEL has 497 rows, 936 columns and 3495 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 372.78 - 0.00 seconds
Cgl0004I processed model has 495 rows, 936 columns (936 integer (936 of which binary)) and 3276 elements
Cbc0038I Initial state - 0 integers unsatisfied sum - 0
Cbc0038I Solution found of -372.78
Cbc003

position                    name             team  price  \
20        GK   Alisson Ramses Becker        Liverpool    5.6   
227      DEF             John Stones  Manchester City    5.3   
444      DEF  Trent Alexander-Arnold        Liverpool    7.9   
57       DEF          Benjamin White          Arsenal    5.8   
165      MID           Heung-Min Son        Tottenham    9.7   
331      MID           Mohamed Salah        Liverpool   13.0   
380      MID         Raheem Sterling          Chelsea    6.9   
69       MID            Bryan Mbeumo        Brentford    6.9   
70       MID             Bukayo Saka          Arsenal    8.7   
119      FWD         Dominic Solanke      Bournemouth    6.5   
363      FWD           Ollie Watkins      Aston Villa    8.5   

     expected_points_with_noise_with_decay  
20                               24.308078  
227                              27.333384  
444                              28.664010  
57                               27.033533  
165                              35.393690  
331                              37.577058  
380                              28.890610  
69                               28.723241  
70                               33.092424  
119                              32.013009  
363                              32.174090

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/884ec74022e240189860e2e5b2308b63-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/884ec74022e240189860e2e5b2308b63-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 502 COLUMNS
At line 6806 RHS
At line 7304 BOUNDS
At line 8241 ENDATA
Problem MODEL has 497 rows, 936 columns and 3495 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 371.382 - 0.00 seconds
Cgl0004I processed model has 495 rows, 936 columns (936 integer (936 of which binary)) and 3276 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.514286
Cbc0038I Solution found of -369.7

...

position                    name             team  price  \
31        GK             André Onana   Manchester Utd    4.8   
263      DEF             Kyle Walker  Manchester City    5.3   
444      DEF  Trent Alexander-Arnold        Liverpool    7.9   
459      DEF          William Saliba          Arsenal    5.4   
165      MID           Heung-Min Son        Tottenham    9.7   
331      MID           Mohamed Salah        Liverpool   13.0   
380      MID         Raheem Sterling          Chelsea    6.9   
69       MID            Bryan Mbeumo        Brentford    6.9   
70       MID             Bukayo Saka          Arsenal    8.7   
105      FWD    Darwin Núñez Ribeiro        Liverpool    7.5   
363      FWD           Ollie Watkins      Aston Villa    8.5   

     expected_points_with_noise_with_decay  
31                               27.002854  
263                              26.879459  
444                              26.370115  
459                              24.670391  
165                              36.594309  
331                              35.441272  
380                              32.312664  
69                               33.054675  
70                               35.939824  
105                              28.363435  
363                              31.674833

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/9187bc40d5a94a12add8f5001d970e5b-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/9187bc40d5a94a12add8f5001d970e5b-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 502 COLUMNS
At line 6806 RHS
At line 7304 BOUNDS
At line 8241 ENDATA
Problem MODEL has 497 rows, 936 columns and 3495 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 373.575 - 0.00 seconds
Cgl0004I processed model has 495 rows, 936 columns (936 integer (936 of which binary)) and 3276 elements
Cbc0038I Initial state - 2 integers unsatisfied sum - 0.52381
Cbc0038I Solution found of -372.59

position                 name             team  price  \
238       GK  José Malheiro de Sá           Wolves    5.0   
422      DEF          Sven Botman    Newcastle Utd    4.7   
451      DEF      Virgil van Dijk        Liverpool    6.1   
50       DEF         Ben Chilwell          Chelsea    5.6   
331      MID        Mohamed Salah        Liverpool   13.0   
370      MID          Pascal Groß         Brighton    6.3   
5        MID   Abdoulaye Doucouré          Everton    5.5   
69       MID         Bryan Mbeumo        Brentford    6.9   
70       MID          Bukayo Saka          Arsenal    8.7   
137      FWD       Erling Haaland  Manchester City   14.0   
363      FWD        Ollie Watkins      Aston Villa    8.5   

     expected_points_with_noise_with_decay  
238                              25.571122  
422                              27.198784  
451                              26.202496  
50                               24.639475  
331                              41.889605  
370                              27.969935  
5                                27.186485  
69                               34.321220  
70                               31.882380  
137                              34.187031  
363                              29.657120

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/ac71866f35ec4ddbb9d4e4e8d3ff63e2-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/ac71866f35ec4ddbb9d4e4e8d3ff63e2-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 502 COLUMNS
At line 6806 RHS
At line 7304 BOUNDS
At line 8241 ENDATA
Problem MODEL has 497 rows, 936 columns and 3495 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 367.755 - 0.00 seconds
Cgl0004I processed model has 495 rows, 936 columns (936 integer (936 of which binary)) and 3276 elements
Cbc0038I Initial state - 4 integers unsatisfied sum - 0.555556
Cbc0038I Pass   1: suminf.    0.1

position                    name            team  price  \
20        GK   Alisson Ramses Becker       Liverpool    5.6   
258      DEF         Kieran Trippier   Newcastle Utd    7.0   
375      DEF        Pervis Estupiñán        Brighton    5.3   
422      DEF             Sven Botman   Newcastle Utd    4.7   
300      MID         Martin Ødegaard         Arsenal    8.5   
331      MID           Mohamed Salah       Liverpool   13.0   
66       MID  Bruno Borges Fernandes  Manchester Utd    8.3   
69       MID            Bryan Mbeumo       Brentford    6.9   
70       MID             Bukayo Saka         Arsenal    8.7   
105      FWD    Darwin Núñez Ribeiro       Liverpool    7.5   
363      FWD           Ollie Watkins     Aston Villa    8.5   

     expected_points_with_noise_with_decay  
20                               26.610343  
258                              26.259357  
375                              25.684175  
422                              27.775483  
300                              31.876847  
331                              32.531591  
66                               31.835215  
69                               34.554778  
70                               33.397852  
105                              31.273103  
363                              31.085200

In [11]:
my_df['dream_team_appearances'] = [sum(team.count(player_id) / simulation_rounds for team in results) for player_id in my_df.index]

In [12]:
print('Most appearances, all players:')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

Most appearances, all players:


name        team_name  expected_points  \
331           Mohamed Salah        Liverpool        63.203479   
70              Bukayo Saka          Arsenal        58.084528   
363           Ollie Watkins      Aston Villa        52.418729   
165           Heung-Min Son        Tottenham        56.178239   
444  Trent Alexander-Arnold        Liverpool        47.225932   
258         Kieran Trippier    Newcastle Utd        45.493056   
69             Bryan Mbeumo        Brentford        49.654186   
206            Jarrod Bowen         West Ham        50.499806   
380         Raheem Sterling          Chelsea        48.178832   
195          James Maddison        Tottenham        48.996550   
137          Erling Haaland  Manchester City        53.203221   
300         Martin Ødegaard          Arsenal        48.688306   
57           Benjamin White          Arsenal        39.367539   
349         Nicolas Jackson          Chelsea        43.250336   
459          William Saliba          Arsenal        38.108686   
73            Callum Wilson    Newcastle Utd        43.243332   
105    Darwin Núñez Ribeiro        Liverpool        42.210071   
375        Pervis Estupiñán         Brighton        38.174011   
108       David Raya Martin          Arsenal        37.901647   
20    Alisson Ramses Becker        Liverpool        38.708823   

     expected_points_with_decay  number_of_games position  price  \
331                    7.447358               10      MID   13.0   
70                     6.922026               10      MID    8.7   
363                    6.194676               10      FWD    8.5   
165                    6.634525               10      MID    9.7   
444                    5.577529               10      DEF    7.9   
258                    5.419818               10      DEF    7.0   
69                     6.073688                9      MID    6.9   
206                    5.967243               10      MID    7.7   
380                    5.589205               10      MID    6.9   
195                    5.791435               10      MID    8.0   
137                    6.403419                9      FWD   14.0   
300                    5.776451               10      MID    8.5   
57                     4.653076               10      DEF    5.8   
349                    5.053802               10      FWD    6.8   
459                    4.510546               10      DEF    5.4   
73                     5.117396               10      FWD    7.9   
105                    5.015258               10      FWD    7.5   
375                    4.451903               10      DEF    5.3   
108                    4.484008               10       GK    4.9   
20                     4.594196               10       GK    5.6   

     dream_team_appearances  
331                   0.890  
70                    0.888  
363                   0.796  
165                   0.708  
444                   0.648  
258                   0.590  
69                    0.574  
206                   0.428  
380                   0.290  
195                   0.280  
137                   0.262  
300                   0.248  
57                    0.202  
349                   0.194  
459                   0.166  
73                    0.160  
105                   0.150  
375                   0.146  
108                   0.138  
20                    0.126

In [13]:
print('GOALKEEPERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='GK']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

GOALKEEPERS


name          team_name  expected_points  \
108          David Raya Martin            Arsenal        37.901647   
20       Alisson Ramses Becker          Liverpool        38.708823   
2               Aaron Ramsdale            Arsenal        37.590208   
354       Norberto Murara Neto        Bournemouth        34.182650   
392             Robert Sánchez            Chelsea        36.399773   
21             Alphonse Areola           West Ham        34.188623   
59                  Bernd Leno             Fulham        34.477193   
348                  Nick Pope      Newcastle Utd        36.117022   
404              Sam Johnstone     Crystal Palace        33.459700   
207               Jason Steele           Brighton        34.706448   
126  Ederson Santana de Moraes    Manchester City        35.853273   
31                 André Onana     Manchester Utd        34.086093   
238        José Malheiro de Sá             Wolves        31.881069   
233            Jordan Pickford            Everton        31.574072   
134   Emiliano Martínez Romero        Aston Villa        31.055711   
154          Guglielmo Vicario          Tottenham        32.314313   
358       Odysseas Vlachodimos  Nottingham Forest        29.898839   
299               Mark Flekken          Brentford        29.626180   
313                Matt Turner  Nottingham Forest        28.542212   
201             James Trafford            Burnley        28.368896   

     expected_points_with_decay  number_of_games position  price  \
108                    4.484008               10       GK    4.9   
20                     4.594196               10       GK    5.6   
2                      4.444686               10       GK    5.0   
354                    4.124028               10       GK    4.5   
392                    4.211686               10       GK    4.6   
21                     4.070396               10       GK    4.3   
59                     4.131833               10       GK    4.7   
348                    4.287402               10       GK    5.5   
404                    4.081589               10       GK    4.6   
207                    4.034773               10       GK    4.3   
126                    4.219766                9       GK    5.5   
31                     3.975329               10       GK    4.8   
238                    3.860741               10       GK    5.0   
233                    3.733618               10       GK    4.4   
134                    3.655095               10       GK    4.9   
154                    3.787468               10       GK    5.2   
358                    3.618472               10       GK    4.5   
299                    3.552628                9       GK    4.5   
313                    3.450862               10       GK    4.1   
201                    3.441601               10       GK    4.5   

     dream_team_appearances  
108                   0.138  
20                    0.126  
2                     0.106  
354                   0.084  
392                   0.082  
21                    0.066  
59                    0.066  
348                   0.066  
404                   0.054  
207                   0.052  
126                   0.044  
31                    0.032  
238                   0.022  
233                   0.020  
134                   0.012  
154                   0.010  
358                   0.008  
299                   0.004  
313                   0.004  
201                   0.002

In [14]:
print('DEFENDERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='DEF']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

DEFENDERS


name        team_name  expected_points  \
444        Trent Alexander-Arnold        Liverpool        47.225932   
258               Kieran Trippier    Newcastle Utd        45.493056   
57                 Benjamin White          Arsenal        39.367539   
459                William Saliba          Arsenal        38.108686   
375              Pervis Estupiñán         Brighton        38.174011   
359           Oleksandr Zinchenko          Arsenal        36.622445   
50                   Ben Chilwell          Chelsea        37.626553   
451               Virgil van Dijk        Liverpool        37.461068   
314                    Matty Cash      Aston Villa        36.156681   
216              Joachim Andersen   Crystal Palace        35.501276   
283                     Luke Shaw   Manchester Utd        36.633497   
277                   Lucas Digne      Aston Villa        35.223568   
150  Gabriel dos Santos Magalhães          Arsenal        36.012700   
422                   Sven Botman    Newcastle Utd        34.689454   
227                   John Stones  Manchester City        33.484058   
446               Tyrick Mitchell   Crystal Palace        31.629679   
271                    Lewis Dunk         Brighton        35.461752   
170               Ibrahima Konaté        Liverpool        31.492063   
373                   Pedro Porro        Tottenham        34.359921   
47                    Axel Disasi          Chelsea        33.218604   

     expected_points_with_decay  number_of_games position  price  \
444                    5.577529               10      DEF    7.9   
258                    5.419818               10      DEF    7.0   
57                     4.653076               10      DEF    5.8   
459                    4.510546               10      DEF    5.4   
375                    4.451903               10      DEF    5.3   
359                    4.327562               10      DEF    5.0   
50                     4.350279               10      DEF    5.6   
451                    4.446656               10      DEF    6.1   
314                    4.264820               10      DEF    5.2   
216                    4.339639               10      DEF    5.1   
283                    4.280386               10      DEF    5.5   
277                    4.149316               10      DEF    4.7   
150                    4.253028               10      DEF    4.8   
422                    4.123682               10      DEF    4.7   
227                    3.940697                9      DEF    5.3   
446                    3.868211               10      DEF    4.7   
271                    4.118741               10      DEF    5.0   
170                    3.739904               10      DEF    4.9   
373                    4.028860               10      DEF    5.3   
47                     3.837214               10      DEF    5.0   

     dream_team_appearances  
444                   0.648  
258                   0.590  
57                    0.202  
459                   0.166  
375                   0.146  
359                   0.106  
50                    0.102  
451                   0.102  
314                   0.100  
216                   0.100  
283                   0.094  
277                   0.094  
150                   0.080  
422                   0.078  
227                   0.038  
446                   0.036  
271                   0.036  
170                   0.026  
373                   0.024  
47                    0.024

In [15]:
print('MIDFIELDERS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='MID']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

MIDFIELDERS


name        team_name  expected_points  \
331                 Mohamed Salah        Liverpool        63.203479   
70                    Bukayo Saka          Arsenal        58.084528   
165                 Heung-Min Son        Tottenham        56.178239   
69                   Bryan Mbeumo        Brentford        49.654186   
206                  Jarrod Bowen         West Ham        50.499806   
380               Raheem Sterling          Chelsea        48.178832   
195                James Maddison        Tottenham        48.996550   
300               Martin Ødegaard          Arsenal        48.688306   
202             James Ward-Prowse         West Ham        43.625028   
66         Bruno Borges Fernandes   Manchester Utd        45.140242   
335                  Moussa Diaby      Aston Villa        42.114591   
265              Leandro Trossard          Arsenal        42.763891   
252                  Kaoru Mitoma         Brighton        42.489123   
370                   Pascal Groß         Brighton        42.143706   
376                    Phil Foden  Manchester City        42.931087   
5              Abdoulaye Doucouré          Everton        39.065049   
93                    Cole Palmer          Chelsea        38.470613   
124                  Eberechi Eze   Crystal Palace        38.712498   
122  Douglas Luiz Soares de Paulo      Aston Villa        38.832910   
120            Dominik Szoboszlai        Liverpool        40.452286   

     expected_points_with_decay  number_of_games position  price  \
331                    7.447358               10      MID   13.0   
70                     6.922026               10      MID    8.7   
165                    6.634525               10      MID    9.7   
69                     6.073688                9      MID    6.9   
206                    5.967243               10      MID    7.7   
380                    5.589205               10      MID    6.9   
195                    5.791435               10      MID    8.0   
300                    5.776451               10      MID    8.5   
202                    5.183353               10      MID    6.1   
66                     5.276204               10      MID    8.3   
335                    4.976067               10      MID    6.8   
265                    5.066912               10      MID    6.5   
252                    4.941206               10      MID    6.6   
370                    4.895310               10      MID    6.3   
376                    5.115850                9      MID    7.5   
5                      4.651560               10      MID    5.5   
93                     4.476766               10      MID    5.2   
124                    4.714171               10      MID    6.1   
122                    4.576775               10      MID    5.6   
120                    4.802843               10      MID    7.1   

     dream_team_appearances  
331                   0.890  
70                    0.888  
165                   0.708  
69                    0.574  
206                   0.428  
380                   0.290  
195                   0.280  
300                   0.248  
202                   0.116  
66                    0.076  
335                   0.058  
265                   0.056  
252                   0.052  
370                   0.050  
376                   0.046  
5                     0.032  
93                    0.024  
124                   0.020  
122                   0.020  
120                   0.018

In [16]:
print('FORWARDS')
display(my_df
        .drop(['team', 'expected_points_with_noise_with_decay'], axis=1)
        [my_df['position']=='FWD']
        .sort_values(by='dream_team_appearances', ascending=False)
        .head(20))

FORWARDS


name          team_name  expected_points  \
363                     Ollie Watkins        Aston Villa        52.418729   
137                    Erling Haaland    Manchester City        53.203221   
349                   Nicolas Jackson            Chelsea        43.250336   
73                      Callum Wilson      Newcastle Utd        43.243332   
105              Darwin Núñez Ribeiro          Liverpool        42.210071   
17                     Alexander Isak      Newcastle Utd        41.864111   
119                   Dominic Solanke        Bournemouth        39.792177   
245                    Julián Álvarez    Manchester City        40.185914   
466                       Yoane Wissa          Brentford        34.353043   
424                     Taiwo Awoniyi  Nottingham Forest        33.537881   
357                   Odsonne Edouard     Crystal Palace        31.333447   
13                Aleksandar Mitrović             Fulham        31.379286   
125                     Eddie Nketiah            Arsenal        32.617745   
118             Dominic Calvert-Lewin            Everton        32.178273   
285                       Lyle Foster            Burnley        29.856485   
92                         Cody Gakpo          Liverpool        32.891348   
307  Matheus Santos Carneiro Da Cunha             Wolves        31.416633   
458                     William Osula      Sheffield Utd        17.196246   
257                     Kieffer Moore        Bournemouth        17.545487   
302                     Mason Burstow            Chelsea        17.379465   

     expected_points_with_decay  number_of_games position  price  \
363                    6.194676               10      FWD    8.5   
137                    6.403419                9      FWD   14.0   
349                    5.053802               10      FWD    6.8   
73                     5.117396               10      FWD    7.9   
105                    5.015258               10      FWD    7.5   
17                     4.983204               10      FWD    7.5   
119                    4.791997               10      FWD    6.5   
245                    4.769082                9      FWD    7.1   
466                    4.138889                9      FWD    5.9   
424                    4.047914               10      FWD    6.4   
357                    3.828519               10      FWD    5.5   
13                     3.760255               10      FWD    7.5   
125                    3.864615               10      FWD    5.7   
118                    3.808456               10      FWD    5.8   
285                    3.620995               10      FWD    5.0   
92                     3.906436               10      FWD    7.2   
307                    3.784315               10      FWD    5.5   
458                    2.062022               10      FWD    4.3   
257                    2.099559               10      FWD    4.7   
302                    2.014970               10      FWD    4.5   

     dream_team_appearances  
363                   0.796  
137                   0.262  
349                   0.194  
73                    0.160  
105                   0.150  
17                    0.124  
119                   0.112  
245                   0.058  
466                   0.012  
424                   0.010  
357                   0.008  
13                    0.006  
125                   0.006  
118                   0.004  
285                   0.004  
92                    0.002  
307                   0.002  
458                   0.000  
257                   0.000  
302                   0.000

In [17]:
players = optimize(my_df, max_price, 'dream_team_appearances', captain_double_points=False)

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Users/jaakkotoivonen/Documents/my_stuff/Fantasy-Premier-League/venv23-24/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/4638047ebeec4aa78a83f134a968633f-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/ml/jr8p__z97xx1jjb90rwg7hfm0000gn/T/4638047ebeec4aa78a83f134a968633f-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 502 COLUMNS
At line 5999 RHS
At line 6497 BOUNDS
At line 7434 ENDATA
Problem MODEL has 497 rows, 936 columns and 3495 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 6.008 - 0.00 seconds
Cgl0004I processed model has 495 rows, 936 columns (936 integer (936 of which binary)) and 3276 elements
Cutoff increment increased from 1e-05 to 0.001998
Cbc0038I Initial state - 0 integers unsatisfied 

position                    name           team  price  \
108       GK       David Raya Martin        Arsenal    4.9   
258      DEF         Kieran Trippier  Newcastle Utd    7.0   
375      DEF        Pervis Estupiñán       Brighton    5.3   
444      DEF  Trent Alexander-Arnold      Liverpool    7.9   
57       DEF          Benjamin White        Arsenal    5.8   
165      MID           Heung-Min Son      Tottenham    9.7   
206      MID            Jarrod Bowen       West Ham    7.7   
331      MID           Mohamed Salah      Liverpool   13.0   
69       MID            Bryan Mbeumo      Brentford    6.9   
70       MID             Bukayo Saka        Arsenal    8.7   
363      FWD           Ollie Watkins    Aston Villa    8.5   

     dream_team_appearances  
108                   0.138  
258                   0.590  
375                   0.146  
444                   0.648  
57                    0.202  
165                   0.708  
206                   0.428  
331                   0.890  
69                    0.574  
70                    0.888  
363                   0.796

In [ ]:
projections[(projections.gameweek==(latest_gameweek+1))].sort_values('expected_points', ascending=False)[['name', 'expected_points']].head(20)

In [ ]:
display(projections[projections.name.str.contains('Saliba')][['name', 'expected_points']])
display(projections[projections.name.str.contains('Saliba')][['expected_points_with_decay']].sum())